In [1]:
%load_ext tensorboard

In [2]:
import tensorflow as tf
from tensorboard.plugins.hparams import api as hp
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras import optimizers
import tensorflow as tf
from tensorflow.keras.layers import Dense, Activation, Flatten, Dropout
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error 
from matplotlib import pyplot as plt
import pandas as pd
import numpy as np
from sklearn import metrics
import seaborn as sns
import shutil
import datetime

In [3]:
data_path = 'data.csv'
df = pd.read_csv(data_path)

dummy_fields = ["Layer-1","Layer-2"]

for each in dummy_fields:
    dummies = pd.get_dummies(df[each], prefix=each, drop_first=False)
    df = pd.concat([df,dummies], axis=1)

fields_to_drop = ["Layer-1","Layer-2"]
df = df.drop(fields_to_drop, axis=1)

tar = ['Core_Real', 'CoreImag', 'TotalPower', 'CorePower','EML', 'CLoss']
# tar = ['CLoss']
x = df[["Layer-1_Au",	"Layer-1_Au+Ta2O5",	"Layer-1_TiO2",	"Layer-2_Au",	"Layer-2_Ta2O5",	"Layer-2_TiO2","Ana-1","Ana-2","Thickness","WaveLength"]]
y = df[tar]


quant_features = tar
scaled_features = {}

for each in quant_features:
    mean, std = y[each].mean(), y[each].std()
    scaled_features[each] = [mean, std]
    y.loc[:, each] = (y[each] - mean)/std 



C:\Users\Administrator\AppData\Local\Temp\ipykernel_8068\498662585.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y.loc[:, each] = (y[each] - mean)/std
C:\Users\Administrator\AppData\Local\Temp\ipykernel_8068\498662585.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y.loc[:, each] = (y[each] - mean)/std
C:\Users\Administrator\AppData\Local\Temp\ipykernel_8068\498662585.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col

In [4]:
X_train, X_test, y_train, y_test = train_test_split(x,y,test_size=0.2, random_state=45)
X_train = X_train.to_numpy()
y_train = y_train.to_numpy()
X_test = X_test.to_numpy()
y_test = y_test.to_numpy()

In [5]:
HP_NUM_UNITS_1 = hp.HParam('Num_units1', hp.Discrete([128, 256, 512]))
HP_NUM_UNITS_2 = hp.HParam('Num_units2', hp.Discrete([32, 64, 128, 256]))
HP_NUM_UNITS_3 = hp.HParam('Num_units3', hp.Discrete([16, 32, 64, 128]))
HP_NUM_UNITS_4 = hp.HParam('Num_units4', hp.Discrete([16, 32, 64, 128]))
HP_NUM_UNITS_5 = hp.HParam('Num_units5', hp.Discrete([8, 16, 32]))

METRIC_ACCURACY = 'mse'

with tf.summary.create_file_writer('logs/hparam_tuning').as_default():
  hp.hparams_config(
    hparams=[HP_NUM_UNITS_1, HP_NUM_UNITS_2, HP_NUM_UNITS_3, HP_NUM_UNITS_4, HP_NUM_UNITS_5],
    metrics=[hp.Metric(METRIC_ACCURACY, display_name='Mean squared error')],
  )

In [6]:
def train_test_model(hparams):

    model = Sequential()
    model.add(Dense(hparams[HP_NUM_UNITS_1], kernel_initializer='normal', input_dim = 10, activation='relu'))
    model.add(Dense(hparams[HP_NUM_UNITS_2], kernel_initializer='normal', activation='relu'))
    model.add(Dense(hparams[HP_NUM_UNITS_3], kernel_initializer='normal', activation='relu'))
    model.add(Dense(hparams[HP_NUM_UNITS_4], kernel_initializer='normal', activation='relu'))
    model.add(Dense(hparams[HP_NUM_UNITS_5], kernel_initializer='normal', activation='relu'))
    model.add(Dense(6, kernel_initializer='normal', activation='linear'))

    #   opt = ""
    #   if hparams[HP_OPTIMIZER] == 'adam':
    #     opt = tf.keras.optimizers.Adam(learning_rate=hparams[HP_LEARNING_RATE])
    #   elif hparams[HP_OPTIMIZER] == 'adagrad':
    #     opt = tf.keras.optimizers.Adagrad(learning_rate=hparams[HP_LEARNING_RATE])
    #   elif hparams[HP_OPTIMIZER] == 'rmsprop':
    #     opt = tf.keras.optimizers.RMSprop(learning_rate=hparams[HP_LEARNING_RATE])
    #   elif hparams[HP_OPTIMIZER] == 'adadelta':
    #     opt = tf.keras.optimizers.Adadelta(learning_rate=hparams[HP_LEARNING_RATE])
    #   elif hparams[HP_OPTIMIZER] == 'adamax':
    #     opt = tf.keras.optimizers.Adamax(learning_rate=hparams[HP_LEARNING_RATE])



    model.compile(
      optimizer=tf.keras.optimizers.Adam(learning_rate=0.003),
      loss='mse',
      metrics=['mae', 'mse'],
    )
    print('------------------------------------------------------------')
    history = model.fit(
        X_train, 
        y_train, 
        epochs=50, 
        batch_size=64, 
        validation_split = 0.2)
    
    accuracy =  pd.DataFrame(history.history)['val_mse'].to_numpy()[-1]
    return accuracy

In [7]:
def run(run_dir, hparams):
  with tf.summary.create_file_writer(run_dir).as_default():
    hp.hparams(hparams)  # record the values used in this trial
    accuracy = train_test_model(hparams)
    tf.summary.scalar(METRIC_ACCURACY, accuracy, step=1)

In [8]:
session_num = 0
cnt=0
for num_units1 in HP_NUM_UNITS_1.domain.values:
    for num_units2 in HP_NUM_UNITS_2.domain.values:
        for num_units3 in HP_NUM_UNITS_3.domain.values:
            for num_units4 in HP_NUM_UNITS_4.domain.values:
                for num_units5 in HP_NUM_UNITS_5.domain.values:
                    hparams = {
                      HP_NUM_UNITS_1: num_units1,
                      HP_NUM_UNITS_2: num_units2,
                      HP_NUM_UNITS_3: num_units3,
                      HP_NUM_UNITS_4: num_units4,
                      HP_NUM_UNITS_5: num_units5
                    }
                    run_name = "run-%d" % session_num
                    print('--- Starting trial: %s' % run_name)
                    print({h.name: hparams[h] for h in hparams})
                    run('logs/hparam_tuning/' + run_name, hparams)
                    session_num += 1
                    


--- Starting trial: run-0
{'Num_units1': 128, 'Num_units2': 32, 'Num_units3': 16, 'Num_units4': 16, 'Num_units5': 8}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 1s 3ms/step - loss: 0.9875 - mae: 0.6693 - mse: 0.9875 - val_loss: 1.0323 - val_mae: 0.6478 - val_mse: 1.0323
Epoch 2/50
56/56 [==============================] - 0s 1ms/step - loss: 0.9495 - mae: 0.6533 - mse: 0.9495 - val_loss: 1.0276 - val_mae: 0.7025 - val_mse: 1.0276
Epoch 3/50
56/56 [==============================] - 0s 1ms/step - loss: 0.8328 - mae: 0.6033 - mse: 0.8328 - val_loss: 0.7218 - val_mae: 0.5492 - val_mse: 0.7218
Epoch 4/50
56/56 [==============================] - 0s 1ms/step - loss: 0.6871 - mae: 0.5347 - mse: 0.6871 - val_loss: 0.6597 - val_mae: 0.4695 - val_mse: 0.6597
Epoch 5/50
56/56 [==============================] - 0s 1ms/step - loss: 0.6023 - mae: 0.4848 - mse: 0.6023 - val_loss: 0.6310 - val_mae: 0.4801 - val_mse: 0.6310
Epoch 6/50
5

56/56 [==============================] - 0s 1ms/step - loss: 0.2136 - mae: 0.2434 - mse: 0.2136 - val_loss: 0.2467 - val_mae: 0.2465 - val_mse: 0.2467
--- Starting trial: run-1
{'Num_units1': 128, 'Num_units2': 32, 'Num_units3': 16, 'Num_units4': 16, 'Num_units5': 16}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 0s 3ms/step - loss: 0.9915 - mae: 0.6684 - mse: 0.9915 - val_loss: 1.0327 - val_mae: 0.6550 - val_mse: 1.0327
Epoch 2/50
56/56 [==============================] - 0s 1ms/step - loss: 0.9690 - mae: 0.6603 - mse: 0.9690 - val_loss: 0.9975 - val_mae: 0.6570 - val_mse: 0.9975
Epoch 3/50
56/56 [==============================] - 0s 1ms/step - loss: 0.9191 - mae: 0.6423 - mse: 0.9191 - val_loss: 0.9294 - val_mae: 0.6261 - val_mse: 0.9294
Epoch 4/50
56/56 [==============================] - 0s 1ms/step - loss: 0.7424 - mae: 0.5621 - mse: 0.7424 - val_loss: 0.6875 - val_mae: 0.4921 - val_mse: 0.6875
Epoch 5/50
56/56 [====

56/56 [==============================] - 0s 1ms/step - loss: 0.1345 - mae: 0.1883 - mse: 0.1345 - val_loss: 0.1864 - val_mae: 0.2180 - val_mse: 0.1864
Epoch 50/50
56/56 [==============================] - 0s 1ms/step - loss: 0.1341 - mae: 0.1906 - mse: 0.1341 - val_loss: 0.1696 - val_mae: 0.2055 - val_mse: 0.1696
--- Starting trial: run-2
{'Num_units1': 128, 'Num_units2': 32, 'Num_units3': 16, 'Num_units4': 16, 'Num_units5': 32}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 1s 3ms/step - loss: 0.9858 - mae: 0.6662 - mse: 0.9858 - val_loss: 1.0212 - val_mae: 0.6526 - val_mse: 1.0212
Epoch 2/50
56/56 [==============================] - 0s 1ms/step - loss: 0.9319 - mae: 0.6490 - mse: 0.9319 - val_loss: 0.9894 - val_mae: 0.6072 - val_mse: 0.9894
Epoch 3/50
56/56 [==============================] - 0s 1ms/step - loss: 0.7439 - mae: 0.5615 - mse: 0.7439 - val_loss: 0.6381 - val_mae: 0.5075 - val_mse: 0.6381
Epoch 4/50
56/56 [===

56/56 [==============================] - 0s 1ms/step - loss: 0.1358 - mae: 0.1948 - mse: 0.1358 - val_loss: 0.1978 - val_mae: 0.2305 - val_mse: 0.1978
Epoch 49/50
56/56 [==============================] - 0s 1ms/step - loss: 0.1425 - mae: 0.2062 - mse: 0.1425 - val_loss: 0.1607 - val_mae: 0.1821 - val_mse: 0.1607
Epoch 50/50
56/56 [==============================] - 0s 1ms/step - loss: 0.1780 - mae: 0.2435 - mse: 0.1780 - val_loss: 0.1770 - val_mae: 0.2078 - val_mse: 0.1770
--- Starting trial: run-3
{'Num_units1': 128, 'Num_units2': 32, 'Num_units3': 16, 'Num_units4': 32, 'Num_units5': 8}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 0s 3ms/step - loss: 0.9875 - mae: 0.6718 - mse: 0.9875 - val_loss: 1.0246 - val_mae: 0.6594 - val_mse: 1.0246
Epoch 2/50
56/56 [==============================] - 0s 1ms/step - loss: 0.9573 - mae: 0.6564 - mse: 0.9573 - val_loss: 1.0048 - val_mae: 0.6802 - val_mse: 1.0048
Epoch 3/50
56/56 [===

56/56 [==============================] - 0s 1ms/step - loss: 0.1467 - mae: 0.2005 - mse: 0.1467 - val_loss: 0.2130 - val_mae: 0.2566 - val_mse: 0.2130
Epoch 48/50
56/56 [==============================] - 0s 2ms/step - loss: 0.1413 - mae: 0.1934 - mse: 0.1413 - val_loss: 0.1865 - val_mae: 0.2078 - val_mse: 0.1865
Epoch 49/50
56/56 [==============================] - 0s 3ms/step - loss: 0.1268 - mae: 0.1742 - mse: 0.1268 - val_loss: 0.1600 - val_mae: 0.1632 - val_mse: 0.1600
Epoch 50/50
56/56 [==============================] - 0s 4ms/step - loss: 0.1428 - mae: 0.1986 - mse: 0.1428 - val_loss: 0.1650 - val_mae: 0.1761 - val_mse: 0.1650
--- Starting trial: run-4
{'Num_units1': 128, 'Num_units2': 32, 'Num_units3': 16, 'Num_units4': 32, 'Num_units5': 16}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 1s 5ms/step - loss: 0.9805 - mae: 0.6661 - mse: 0.9805 - val_loss: 1.0295 - val_mae: 0.6933 - val_mse: 1.0295
Epoch 2/50
56/56 [=

...

--- Starting trial: run-572
{'Num_units1': 512, 'Num_units2': 256, 'Num_units3': 128, 'Num_units4': 64, 'Num_units5': 32}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 1s 4ms/step - loss: 1.0690 - mae: 0.7012 - mse: 1.0690 - val_loss: 1.0435 - val_mae: 0.6827 - val_mse: 1.0435
Epoch 2/50
56/56 [==============================] - 0s 3ms/step - loss: 0.9788 - mae: 0.6664 - mse: 0.9788 - val_loss: 1.0237 - val_mae: 0.6550 - val_mse: 1.0237
Epoch 3/50
56/56 [==============================] - 0s 3ms/step - loss: 0.9648 - mae: 0.6611 - mse: 0.9648 - val_loss: 1.0073 - val_mae: 0.6624 - val_mse: 1.0073
Epoch 4/50
56/56 [==============================] - 0s 3ms/step - loss: 0.9628 - mae: 0.6532 - mse: 0.9628 - val_loss: 0.9926 - val_mae: 0.6596 - val_mse: 0.9926
Epoch 5/50
56/56 [==============================] - 0s 3ms/step - loss: 0.9349 - mae: 0.6469 - mse: 0.9349 - val_loss: 0.9747 - val_mae: 0.6405 - val_mse: 0.9747
Epoch 6

56/56 [==============================] - 0s 3ms/step - loss: 0.2156 - mae: 0.2576 - mse: 0.2156 - val_loss: 0.2520 - val_mae: 0.2688 - val_mse: 0.2520
--- Starting trial: run-573
{'Num_units1': 512, 'Num_units2': 256, 'Num_units3': 128, 'Num_units4': 128, 'Num_units5': 8}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 1s 4ms/step - loss: 1.3581 - mae: 0.7098 - mse: 1.3581 - val_loss: 1.0597 - val_mae: 0.6642 - val_mse: 1.0597
Epoch 2/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0061 - mae: 0.6689 - mse: 1.0061 - val_loss: 1.0596 - val_mae: 0.6632 - val_mse: 1.0596
Epoch 3/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0059 - mae: 0.6676 - mse: 1.0059 - val_loss: 1.0597 - val_mae: 0.6619 - val_mse: 1.0597
Epoch 4/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6674 - mse: 1.0058 - val_loss: 1.0598 - val_mae: 0.6612 - val_mse: 1.0598
Epoch 5/50
56/56 [

56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6639 - mse: 1.0058 - val_loss: 1.0597 - val_mae: 0.6595 - val_mse: 1.0597
Epoch 50/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0059 - mae: 0.6629 - mse: 1.0059 - val_loss: 1.0596 - val_mae: 0.6587 - val_mse: 1.0596
--- Starting trial: run-574
{'Num_units1': 512, 'Num_units2': 256, 'Num_units3': 128, 'Num_units4': 128, 'Num_units5': 16}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 1s 4ms/step - loss: 1.1015 - mae: 0.7005 - mse: 1.1015 - val_loss: 1.0595 - val_mae: 0.6598 - val_mse: 1.0595
Epoch 2/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6656 - mse: 1.0058 - val_loss: 1.0595 - val_mae: 0.6596 - val_mse: 1.0595
Epoch 3/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0057 - mae: 0.6644 - mse: 1.0057 - val_loss: 1.0596 - val_mae: 0.6589 - val_mse: 1.0596
Epoch 4/50
56/56

56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6636 - mse: 1.0058 - val_loss: 1.0597 - val_mae: 0.6572 - val_mse: 1.0597
Epoch 49/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6630 - mse: 1.0058 - val_loss: 1.0597 - val_mae: 0.6587 - val_mse: 1.0597
Epoch 50/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6634 - mse: 1.0058 - val_loss: 1.0596 - val_mae: 0.6595 - val_mse: 1.0596
--- Starting trial: run-575
{'Num_units1': 512, 'Num_units2': 256, 'Num_units3': 128, 'Num_units4': 128, 'Num_units5': 32}
------------------------------------------------------------
Epoch 1/50
56/56 [==============================] - 1s 4ms/step - loss: 1.2167 - mae: 0.7301 - mse: 1.2167 - val_loss: 1.0598 - val_mae: 0.6544 - val_mse: 1.0598
Epoch 2/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0061 - mae: 0.6607 - mse: 1.0061 - val_loss: 1.0596 - val_mae: 0.6564 - val_mse: 1.0596
Epoch 3/50
56/5

56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6654 - mse: 1.0058 - val_loss: 1.0598 - val_mae: 0.6595 - val_mse: 1.0598
Epoch 48/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0061 - mae: 0.6636 - mse: 1.0061 - val_loss: 1.0598 - val_mae: 0.6610 - val_mse: 1.0598
Epoch 49/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0058 - mae: 0.6658 - mse: 1.0058 - val_loss: 1.0597 - val_mae: 0.6584 - val_mse: 1.0597
Epoch 50/50
56/56 [==============================] - 0s 3ms/step - loss: 1.0059 - mae: 0.6618 - mse: 1.0059 - val_loss: 1.0599 - val_mae: 0.6595 - val_mse: 1.0599


In [ ]:
%tensorboard --logdir logs/hparam_tuning